The goal of this notebook is to understand a chunking strategy to use properly docling converted document. 
Indeed, with a quick test using DoclingReader in llama-index, it seems that some information in DoclingDocument are lost when using llama-index. This make necessary some sperimentation with both version (Docling and DoclingReader in llama-index) to find the most adaptable solution.

In [1]:
from pathlib import Path

all_files_gen = Path("./data/").rglob("*")
all_files = [f.resolve() for f in all_files_gen]
all_pdf_files = [f for f in all_files if f.suffix.lower() == ".pdf"]
len(all_pdf_files)

3

In [13]:
from docling.document_converter import DocumentConverter

doc = DocumentConverter().convert(all_pdf_files[1])
doc

ConversionResult(input=InputDocument(file=PosixPath('/Users/rauldemaio/Projects Local/agent_rag/data/bolletta.pdf'), document_hash='de4e605af50a375cf649ecce534554656d3acae529c97253a242c70b3da49188', valid=True, limits=DocumentLimits(max_num_pages=9223372036854775807, max_file_size=9223372036854775807, page_range=(1, 9223372036854775807)), format=<InputFormat.PDF: 'pdf'>, filesize=697882, page_count=5), status=<ConversionStatus.SUCCESS: 'success'>, errors=[], pages=[Page(page_no=0, size=Size(width=595.2750244140625, height=841.8889770507812), cells=[PdfTextCell(index=0, rgba=ColorRGBA(r=0, g=0, b=0, a=255), rect=BoundingRectangle(r_x0=320.907, r_y0=58.847977050781196, r_x1=367.397, r_y1=58.847977050781196, r_x2=367.397, r_y2=50.52997705078121, r_x3=320.907, r_y3=50.52997705078121, coord_origin=<CoordOrigin.TOPLEFT: 'TOPLEFT'>), text='rif. bolletta*', orig='rif. bolletta*', text_direction=<TextDirection.LEFT_TO_RIGHT: 'left_to_right'>, confidence=1.0, from_ocr=False, rendering_mode=<PdfC

Let's start analysing the result of DocumentConverter

In [5]:
for key,value in doc.model_dump().items():
    print(f'Component {key} - Value:  {value}')
    print('##############################################')

Component input - Value:  {'file': PosixPath('/Users/rauldemaio/Projects Local/agent_rag/data/bonifico.pdf'), 'document_hash': '4ba901717f73b2ec7617e4fd676460c0d4ee2aabe75d2d4317453c39f0528bf7', 'valid': True, 'limits': {'max_num_pages': 9223372036854775807, 'max_file_size': 9223372036854775807, 'page_range': (1, 9223372036854775807)}, 'format': <InputFormat.PDF: 'pdf'>, 'filesize': 7680, 'page_count': 2}
##############################################
Component status - Value:  ConversionStatus.SUCCESS
##############################################
Component errors - Value:  []
##############################################
Component pages - Value:  [{'page_no': 0, 'size': {'width': 595.280029296875, 'height': 841.8800048828125}, 'cells': [{'id': 0, 'text': 'Eseguito Bonifico Europeo Unico in data 20.11.2024', 'bbox': {'l': 72.08000354743776, 't': 135.5440007861405, 'r': 337.436016607009, 'b': 146.34400084877927, 'coord_origin': <CoordOrigin.TOPLEFT: 'TOPLEFT'>}}, {'id': 1, 'text': '20

* input: contains the input metadata
* status: contains the conversion status
* errors: in this case no error but I assume it contains the list of errors encountered during conversion
* pages: it is the list of all converted pages
* assembled: it is interesting. Seems to be the list of all assembled extract components
* document: it is the DoclingDocument object itself

In [12]:
for key,value in doc.assembled.model_dump().items():
    print(f'Component {key} - Value:  {value}')
    print('##############################################')

Component elements - Value:  [{'label': <DocItemLabel.KEY_VALUE_REGION: 'key_value_region'>, 'id': 59, 'page_no': 0, 'cluster': {'id': 59, 'label': <DocItemLabel.KEY_VALUE_REGION: 'key_value_region'>, 'bbox': {'l': 72.08000354743776, 't': 135.5440007861405, 'r': 518.7880255322993, 'b': 758.5740043996468, 'coord_origin': <CoordOrigin.TOPLEFT: 'TOPLEFT'>}, 'confidence': 0.5649534463882446, 'cells': [{'id': 0, 'text': 'Eseguito Bonifico Europeo Unico in data 20.11.2024', 'bbox': {'l': 72.08000354743776, 't': 135.5440007861405, 'r': 337.436016607009, 'b': 146.34400084877927, 'coord_origin': <CoordOrigin.TOPLEFT: 'TOPLEFT'>}}, {'id': 1, 'text': '20.11.2024 21:38', 'bbox': {'l': 72.08000354743776, 't': 149.42400086664293, 'r': 157.07600773054014, 'b': 160.22400092928183, 'coord_origin': <CoordOrigin.TOPLEFT: 'TOPLEFT'>}}, {'id': 2, 'text': 'Internet Banking', 'bbox': {'l': 72.08000354743776, 't': 180.7740010484696, 'r': 153.06800753328528, 'b': 191.57400111110826, 'coord_origin': <CoordOrigi

In [6]:
from docling.chunking import BaseChunker,HybridChunker, HierarchicalChunker

In [7]:
chunker = HybridChunker()
chunk_iter = chunker.chunk(dl_doc=doc.document)

Token indices sequence length is longer than the specified maximum sequence length for this model (557 > 512). Running this sequence through the model will result in indexing errors


In [8]:
for i, chunk in enumerate(chunk_iter):
    print(f"=== {i} ===")
    print(f"chunk.text:\n{repr(f'{chunk.text[:300]}…')}")

    enriched_text = chunker.serialize(chunk=chunk)
    print(f"chunker.serialize(chunk):\n{repr(f'{enriched_text[:300]}…')}")
    print()


=== 0 ===
chunk.text:
"Internet Banking\nVi confermiamo il Vostro ordine di Bonifico Europeo Unico in data 20.11.2024\nNumero ordine\nINTER20241120BOSBE350192748\nOrdinante De Maio Raul - Pantaleo Rossella Filiale ROMA-TUSCOLANA\nN. C/C\n1000/00014233\nDati dell'operazione\nBeneficiario\nEDIL FIORINI SNC\nIndirizzo\nLocalit\n-\nPaese\n…"
chunker.serialize(chunk):
'Eseguito Bonifico Europeo Unico in data 20.11.2024 20.11.2024 21:38\nInternet Banking\nVi confermiamo il Vostro ordine di Bonifico Europeo Unico in data 20.11.2024\nNumero ordine\nINTER20241120BOSBE350192748\nOrdinante De Maio Raul - Pantaleo Rossella Filiale ROMA-TUSCOLANA\nN. C/C\n1000/00014233\nDati dell…'

=== 1 ===
chunk.text:
'operazione" secondo le modalita\' concordate in sede di stipula del contratto di conto corrente e/o di successive variazioni concordate, nel quale potra\' trovare ogni dettaglio in proposito. In sede di liquidazione periodica di queste spese potra\' verificare il dettaglio dei conteggi, che viene 

In [9]:
for chunk in list(chunker.chunk(dl_doc=doc.document)):
    print(chunk.model_dump().keys())
    print(chunk.model_dump()['meta'].keys())
    print(chunk.model_dump()['meta'])
    break

dict_keys(['text', 'meta'])
dict_keys(['schema_name', 'version', 'doc_items', 'headings', 'captions', 'origin'])
{'schema_name': 'docling_core.transforms.chunker.DocMeta', 'version': '1.0.0', 'doc_items': [{'self_ref': '#/texts/1', 'parent': {'cref': '#/groups/0'}, 'children': [], 'content_layer': <ContentLayer.BODY: 'body'>, 'label': <DocItemLabel.TEXT: 'text'>, 'prov': [{'page_no': 1, 'bbox': {'l': 72.08, 't': 661.106, 'r': 153.068, 'b': 650.306, 'coord_origin': <CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>}, 'charspan': (0, 16)}]}, {'self_ref': '#/texts/2', 'parent': {'cref': '#/groups/0'}, 'children': [], 'content_layer': <ContentLayer.BODY: 'body'>, 'label': <DocItemLabel.TEXT: 'text'>, 'prov': [{'page_no': 1, 'bbox': {'l': 72.08, 't': 644.686, 'r': 455.708, 'b': 633.886, 'coord_origin': <CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>}, 'charspan': (0, 76)}]}, {'self_ref': '#/texts/3', 'parent': {'cref': '#/groups/0'}, 'children': [], 'content_layer': <ContentLayer.BODY: 'body'>, 'label': <DocIte

In [61]:
chunker = HierarchicalChunker()


In [62]:
chunk_iter = list(chunker.chunk(dl_doc=doc.document))

for i, chunk in enumerate(chunk_iter):
    print(f"=== {i} ===")
    print(f"chunk.text:\n{repr(f'{chunk.text}…')}")

    enriched_text = chunker.serialize(chunk=chunk)
    print(f"chunker.serialize(chunk):\n{repr(f'{enriched_text}…')}")
    print()


=== 0 ===
chunk.text:
'rif. bolletta*…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\nrif. bolletta*…'

=== 1 ===
chunk.text:
'2444192752…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\n2444192752…'

=== 2 ===
chunk.text:
'03.12.2024…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\n03.12.2024…'

=== 3 ===
chunk.text:
'900 267 786 714…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\n900 267 786 714…'

=== 4 ===
chunk.text:
'numero cliente…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\nnumero cliente…'

=== 5 ===
chunk.text:
'data di emissione…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\ndata di emissione…'

=== 6 ===
chunk.text:
'*numero fattura elettronica valido ai fini fiscali (ex. art. 21 D.P.R.N.633/72 IVA e art. 1 D.M. 370 24.10.2000)…'
chunker.serialize(chunk):
'da 1 Ottobre 2024 a 30 Novembre 2024\n*numero fattura elettronica valido ai fini fiscali (ex. art. 21 D.P

In [65]:
doc.document.texts[:10]

[TextItem(self_ref='#/texts/0', parent=RefItem(cref='#/pictures/1'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=1, bbox=BoundingBox(l=74.871, t=711.615, r=190.869, b=677.633, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 20))], orig='La mia bolletta luce', text='La mia bolletta luce', formatting=None, hyperlink=None),
 SectionHeaderItem(self_ref='#/texts/1', parent=RefItem(cref='#/body'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.SECTION_HEADER: 'section_header'>, prov=[ProvenanceItem(page_no=1, bbox=BoundingBox(l=31.181, t=648.173, r=135.223, b=638.258, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 22))], orig='Periodo di riferimento', text='Periodo di riferimento', formatting=None, hyperlink=None, level=1),
 SectionHeaderItem(self_ref='#/texts/2', parent=RefItem(cref='#/body'), children=[], content_layer=<ContentLayer.BODY: 'body'>, 

In [63]:
list(chunk_iter)

[DocChunk(text='rif. bolletta*', meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', doc_items=[TextItem(self_ref='#/texts/3', parent=RefItem(cref='#/groups/0'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text'>, prov=[ProvenanceItem(page_no=1, bbox=BoundingBox(l=320.907, t=791.359, r=367.397, b=783.041, coord_origin=<CoordOrigin.BOTTOMLEFT: 'BOTTOMLEFT'>), charspan=(0, 14))], orig='rif. bolletta*', text='rif. bolletta*', formatting=None, hyperlink=None)], headings=['da 1 Ottobre 2024 a 30 Novembre 2024'], captions=None, origin=DocumentOrigin(mimetype='application/pdf', binary_hash=11692126433699991944, filename='bolletta.pdf', uri=None))),
 DocChunk(text='2444192752', meta=DocMeta(schema_name='docling_core.transforms.chunker.DocMeta', version='1.0.0', doc_items=[TextItem(self_ref='#/texts/4', parent=RefItem(cref='#/groups/0'), children=[], content_layer=<ContentLayer.BODY: 'body'>, label=<DocItemLabel.TEXT: 'text

---

Some references:

* [Recursive Retriever in Llama-index](https://docs.llamaindex.ai/en/stable/examples/query_engine/pdf_tables/recursive_retriever/?utm_source=pocket_shared): The concept of recursive retrieval is that we not only explore the directly most relevant nodes, but also explore node relationships to additional retrievers/query engines and execute them. For instance, a node may represent a concise summary of a structured table, and link to a SQL/Pandas query engine over that structured table. Then if the node is retrieved, we want to also query the underlying query engine for the answer.
* [Recursive Retriever and Document Agents](https://docs.llamaindex.ai/en/stable/examples/query_engine/recursive_retriever_agents/): This guide shows how to combine recursive retrieval and "document agents" for advanced decision making over heterogeneous documents.
* [Joint Tabular/Semantic QA over Tesla 10K](https://docs.llamaindex.ai/en/stable/examples/query_engine/sec_tables/tesla_10q_table/): In this example, we show how to ask questions over 10K with understanding of both the unstructured text as well as embedded tables.
* [Example of RAG with texts and tables](https://howaibuildthis.substack.com/p/a-guide-to-processing-tables-in-rag?utm_source=pocket_shared)
* [The same thing explained better but with langchain](https://github.com/langchain-ai/langchain/blob/master/cookbook/Semi_Structured_RAG.ipynb?ref=blog.langchain.dev&utm_source=pocket_saves)

Some notes:
* with Docling we have full control on .pdf parsing
* if Docling API in Llama index (aka Docling Reader and DoclingNodeParser) does not satisfy our requirements for tables we can build customlly our nodes
    * differentiate between table nodes and text nodes
    * add nodes relationship 
    * integrate metadata from docling metadata
* in a second step we may look to integrate summaries and recursive retrievers

There are two key points that we need to understand and solve:
* how to combine text nodes based on their position
* how to link text nodes and tables nodes to preserve page order

---

In [3]:
from docling.document_converter import DocumentConverter

doc = DocumentConverter().convert(all_pdf_files[0])
doc

ConversionResult(input=InputDocument(file=PosixPath('/Users/rauldemaio/Projects Local/agent_rag/data/bonifico.pdf'), document_hash='4ba901717f73b2ec7617e4fd676460c0d4ee2aabe75d2d4317453c39f0528bf7', valid=True, limits=DocumentLimits(max_num_pages=9223372036854775807, max_file_size=9223372036854775807, page_range=(1, 9223372036854775807)), format=<InputFormat.PDF: 'pdf'>, filesize=7680, page_count=2), status=<ConversionStatus.SUCCESS: 'success'>, errors=[], pages=[Page(page_no=0, size=Size(width=595.280029296875, height=841.8800048828125), cells=[PdfTextCell(index=0, rgba=ColorRGBA(r=0, g=0, b=0, a=255), rect=BoundingRectangle(r_x0=72.08, r_y0=146.34400488281256, r_x1=337.436, r_y1=146.34400488281256, r_x2=337.436, r_y2=135.5440048828125, r_x3=72.08, r_y3=135.5440048828125, coord_origin=<CoordOrigin.TOPLEFT: 'TOPLEFT'>), text='Eseguito Bonifico Europeo Unico in data 20.11.2024', orig='Eseguito Bonifico Europeo Unico in data 20.11.2024', text_direction=<TextDirection.LEFT_TO_RIGHT: 'left

In [25]:
doc.document.model_dump().keys()

dict_keys(['schema_name', 'version', 'name', 'origin', 'furniture', 'body', 'groups', 'texts', 'pictures', 'tables', 'key_value_items', 'form_items', 'pages'])

In [22]:
def load_pdf(pdf_path: str):
    """
    Load PDF using Docling and return a Document object
    """
    print(f"Loading PDF: {pdf_path}")
    doc = DocumentConverter().convert(pdf_path).document
    return doc

In [28]:
load_pdf(all_pdf_files[0])

Loading PDF: /Users/rauldemaio/Projects Local/agent_rag/data/bonifico.pdf


DoclingDocument(schema_name='DoclingDocument', version='1.3.0', name='bonifico', origin=DocumentOrigin(mimetype='application/pdf', binary_hash=1676812655808121847, filename='bonifico.pdf', uri=None), furniture=GroupItem(self_ref='#/furniture', parent=None, children=[], content_layer=<ContentLayer.FURNITURE: 'furniture'>, name='_root_', label=<GroupLabel.UNSPECIFIED: 'unspecified'>), body=GroupItem(self_ref='#/body', parent=None, children=[RefItem(cref='#/pictures/0'), RefItem(cref='#/groups/0'), RefItem(cref='#/texts/51'), RefItem(cref='#/texts/52')], content_layer=<ContentLayer.BODY: 'body'>, name='_root_', label=<GroupLabel.UNSPECIFIED: 'unspecified'>), groups=[GroupItem(self_ref='#/groups/0', parent=RefItem(cref='#/body'), children=[RefItem(cref='#/texts/0'), RefItem(cref='#/texts/1'), RefItem(cref='#/texts/2'), RefItem(cref='#/texts/3'), RefItem(cref='#/texts/4'), RefItem(cref='#/texts/5'), RefItem(cref='#/texts/6'), RefItem(cref='#/texts/7'), RefItem(cref='#/texts/8'), RefItem(cre

In [32]:
def extract_items(doc):
    """
    Extract items (such as text and tables) from Document object
    Returns: tuple of (text_blocks, tables, pictures)
    """
    print("Extracting items...")
    
    # Extract text
    text_blocks = doc.texts

    # Extract tables
    table_blocks = doc.tables

    # Extract pictures
    picture_blocks = doc.pictures
    
    return text_blocks, table_blocks, picture_blocks

In [34]:
text_blocks, table_block, picture_blocks = extract_items(doc.document)

Extracting items...


In [ ]:
def collapse_small_text_chunks(text_blocks, 
                              min_words: int = 20,
                              max_distance: float = 100):
    """
    Collapse small adjacent text blocks that are close to each other
    
    Args:
        text_blocks: List of text blocks from extraction
        min_words: Minimum number of words to consider a block as "small"
        max_distance: Maximum distance (in pixels) to consider blocks as "close"
        
    Returns:
        List of text blocks with small blocks merged
    """
    print("Collapsing small text chunks...")

    collapsed_blocks = []
    current_block = text_blocks[0].copy()
    current_text = current_block['text']
    current_ref = current_block['self_ref']
    current_parent = current_block['parent'].cref
    current_content_layer = current_block['content_layer']
    current_label = current_block['label']
    current_page = current_block['page']

    for next_block in text_blocks[1:].copy():

        next_text = next_block['text']
        next_ref = next_block['self_ref']
        next_parent = next_block['parent'].cref
        next_content_layer = next_block['content_layer']
        next_label = next_block['label']
        next_page = next_block['page']

        same_page = current_page == next_page
        same_parent = current_parent == next_parent
        same_content_layer = current_content_layer == next_content_layer
        


Collapsing small text chunks...


TypeError: 'BoundingBox' object is not subscriptable

**Idea:** instead of rewriting a Chunker or NodeParser, we can try augmenting the result of Docling's HierarchicalChuncker and integrate Table nodes and related summaries. 